In [1]:
# usual things
import pandas as pd
import numpy as np
%matplotlib inline

In [7]:
#!pip install xlrd
df = pd.read_excel('https://query.data.world/s/ivl45pdpubos6jpsii3djsjwm2pcjv', skiprows=5)

# if verify issues:
#!open /Applications/Python/Python 3.7/Install/ Certificates.command
#https://timonweb.com/tutorials/fixing-certificate_verify_failed-error-when-trying-requests_html-out-on-mac/

# for verify errors - trying:
#import requests
#df = pd.read_excel(requests.get('https://query.data.world/s/ivl45pdpubos6jpsii3djsjwm2pcjv',verify=False), skiprows=5)
#requests.get('https://query.data.world/s/ivl45pdpubos6jpsii3djsjwm2pcjv', verify=False).text


In [12]:
df.head()

DRG Definition  Provider Id  \
0  001 - HEART TRANSPLANT OR IMPLANT OF HEART ASS...        10033   
1  001 - HEART TRANSPLANT OR IMPLANT OF HEART ASS...        30103   
2  001 - HEART TRANSPLANT OR IMPLANT OF HEART ASS...        50108   
3  001 - HEART TRANSPLANT OR IMPLANT OF HEART ASS...        50262   
4  001 - HEART TRANSPLANT OR IMPLANT OF HEART ASS...        50441   

                          Provider Name   Provider Street Address  \
0        UNIVERSITY OF ALABAMA HOSPITAL     619 SOUTH 19TH STREET   
1                  MAYO CLINIC HOSPITAL  5777 EAST MAYO BOULEVARD   
2               SUTTER GENERAL HOSPITAL             2801 L STREET   
3  RONALD REAGAN U C L A MEDICAL CENTER        757 WESTWOOD PLAZA   
4                     STANFORD HOSPITAL         300 PASTEUR DRIVE   

  Provider City Provider State  Provider Zip Code  \
0    BIRMINGHAM             AL              35233   
1       PHOENIX             AZ              85054   
2    SACRAMENTO             CA              95816   
3   LOS ANGELES             CA              90095   
4      STANFORD             CA              94305   

  Hospital Referral Region (HRR) Description  Total Discharges  \
0                            AL - Birmingham                13   
1                               AZ - Phoenix                20   
2                            CA - Sacramento                25   
3                           CA - Los Angeles                14   
4                      CA - San Mateo County                23   

   Average Covered Charges  Average Total Payments  Average Medicare Payments  
0             1.172866e+06           251876.307692              244457.923077  
1             4.375313e+05           240422.800000              133509.550000  
2             8.156741e+05           233197.480000              221681.800000  
3             1.499044e+06           415968.785714              366608.928571  
4             2.238699e+06           420865.478261              403453.652174

In [13]:
df.dtypes

DRG Definition                                 object
Provider Id                                     int64
Provider Name                                  object
Provider Street Address                        object
Provider City                                  object
Provider State                                 object
Provider Zip Code                               int64
Hospital Referral Region (HRR) Description     object
Total Discharges                                int64
Average Covered Charges                       float64
Average Total Payments                        float64
Average Medicare Payments                     float64
dtype: object

In [14]:
df.describe()

Provider Id  Provider Zip Code  Total Discharges  \
count  202656.000000      202656.000000     202656.000000   
mean   255322.552749       47029.141698         36.011196   
std    150834.203550       27792.935433         48.864835   
min     10001.000000        1040.000000         11.000000   
25%    110082.000000       25301.000000         14.000000   
50%    240093.000000       43701.000000         22.000000   
75%    380014.000000       71603.000000         39.000000   
max    670088.000000       99801.000000       3855.000000   

       Average Covered Charges  Average Total Payments  \
count             2.026560e+05           202656.000000   
mean              5.258934e+04            13168.560144   
std               6.244522e+04            13772.839671   
min               1.367652e+03             2320.482759   
25%               2.094930e+04             6258.925806   
50%               3.463380e+04             9180.169753   
75%               6.076193e+04            14631.466690   
max               2.238699e+06           434396.000000   

       Average Medicare Payments  
count              202656.000000  
mean                11218.465217  
std                 12279.103622  
min                  1329.909091  
25%                  5011.979167  
50%                  7714.654762  
75%                 12472.680288  
max                403453.652174

In [15]:
# what is the number of unique surgeries being performed?
df['DRG Definition'].unique().size

564

In [16]:
# how many providers (hospitals) are in this dataset?
df['Provider Name'].unique().size

3151

In [18]:
# how many states in dataset?
df['Provider State'].unique()

array([u'AL', u'AZ', u'CA', u'CT', u'DC', u'FL', u'GA', u'IL', u'IN',
       u'KY', u'LA', u'MA', u'MI', u'MN', u'MO', u'NE', u'NJ', u'NY',
       u'NC', u'OH', u'OK', u'PA', u'SC', u'TN', u'TX', u'VA', u'WA',
       u'WI', u'AK', u'AR', u'CO', u'DE', u'ID', u'IA', u'KS', u'ME',
       u'MD', u'MS', u'NV', u'NH', u'NM', u'ND', u'OR', u'RI', u'UT',
       u'VT', u'WV', u'HI', u'SD', u'MT', u'WY'], dtype=object)

In [24]:
# what is the most common surgery? 
# => how many folks are dischaged after each surgery?

most_common = df.groupby("DRG Definition")['Total Discharges'].sum()
most_common

# lets put most common on top
most_common = df.groupby("DRG Definition")['Total Discharges'].sum().sort_values(ascending=False)
most_common[:5].index.values


array([u'470 - MAJOR JOINT REPLACEMENT OR REATTACHMENT OF LOWER EXTREMITY W/O MCC',
       u'871 - SEPTICEMIA OR SEVERE SEPSIS W/O MV 96+ HOURS W MCC',
       u'291 - HEART FAILURE & SHOCK W MCC',
       u'292 - HEART FAILURE & SHOCK W CC',
       u'392 - ESOPHAGITIS, GASTROENT & MISC DIGEST DISORDERS W/O MCC'],
      dtype=object)

# Lets format for MarketMap

In [26]:
total_discharges = df.groupby(["DRG Definition", "Provider State"])["Total Discharges"].sum().unstack()
total_discharges

Provider State                                        AK     AL     AR     AZ  \
DRG Definition                                                                  
001 - HEART TRANSPLANT OR IMPLANT OF HEART ASSI...   NaN   13.0    NaN   20.0   
002 - HEART TRANSPLANT OR IMPLANT OF HEART ASSI...   NaN    NaN    NaN    NaN   
003 - ECMO OR TRACH W MV 96+ HRS OR PDX EXC FAC...  12.0  237.0  128.0  200.0   
004 - TRACH W MV 96+ HRS OR PDX EXC FACE, MOUTH...  11.0  257.0  129.0  127.0   
005 - LIVER TRANSPLANT W MCC OR INTESTINAL TRAN...   NaN   16.0    NaN   17.0   
006 - LIVER TRANSPLANT W/O MCC                       NaN    NaN    NaN    NaN   
007 - LUNG TRANSPLANT                                NaN    NaN    NaN   22.0   
008 - SIMULTANEOUS PANCREAS/KIDNEY TRANSPLANT        NaN    NaN    NaN    NaN   
011 - TRACHEOSTOMY FOR FACE,MOUTH & NECK DIAGNO...   NaN   15.0    NaN   13.0   
012 - TRACHEOSTOMY FOR FACE,MOUTH & NECK DIAGNO...   NaN   47.0   14.0   12.0   
013 - TRACHEOSTOMY FOR FACE,MOUTH & NECK DIAGNO...   NaN   13.0   12.0    NaN   
014 - ALLOGENEIC BONE MARROW TRANSPLANT              NaN   13.0    NaN   18.0   
016 - AUTOLOGOUS BONE MARROW TRANSPLANT W CC/MCC     NaN   25.0   28.0   49.0   
017 - AUTOLOGOUS BONE MARROW TRANSPLANT W/O CC/MCC   NaN   11.0    NaN   15.0   
020 - INTRACRANIAL VASCULAR PROCEDURES W PDX HE...   NaN   14.0   15.0    NaN   
023 - CRANIO W MAJOR DEV IMPL/ACUTE COMPLEX CNS...   NaN   56.0   35.0   60.0   
024 - CRANIO W MAJOR DEV IMPL/ACUTE COMPLEX CNS...   NaN    NaN    NaN   32.0   
025 - CRANIOTOMY & ENDOVASCULAR INTRACRANIAL PR...   NaN  249.0  227.0  435.0   
026 - CRANIOTOMY & ENDOVASCULAR INTRACRANIAL PR...   NaN   88.0   62.0  164.0   
027 - CRANIOTOMY & ENDOVASCULAR INTRACRANIAL PR...   NaN  130.0   83.0  206.0   
028 - SPINAL PROCEDURES W MCC                        NaN    NaN    NaN   14.0   
029 - SPINAL PROCEDURES W CC OR SPINAL NEUROSTI...   NaN   26.0    NaN   29.0   
030 - SPINAL PROCEDURES W/O CC/MCC                   NaN    NaN    NaN   13.0   
031 - VENTRICULAR SHUNT PROCEDURES W MCC             NaN   11.0   11.0    NaN   
032 - VENTRICULAR SHUNT PROCEDURES W CC              NaN   11.0    NaN   40.0   
033 - VENTRICULAR SHUNT PROCEDURES W/O CC/MCC        NaN   27.0   17.0   34.0   
034 - CAROTID ARTERY STENT PROCEDURE W MCC           NaN    NaN    NaN    NaN   
035 - CAROTID ARTERY STENT PROCEDURE W CC            NaN   14.0   11.0   13.0   
036 - CAROTID ARTERY STENT PROCEDURE W/O CC/MCC      NaN   81.0   16.0   70.0   
037 - EXTRACRANIAL PROCEDURES W MCC                  NaN   23.0   13.0   17.0   
...                                                  ...    ...    ...    ...   
921 - COMPLICATIONS OF TREATMENT W/O CC/MCC          NaN    NaN   11.0    NaN   
923 - OTHER INJURY, POISONING & TOXIC EFFECT DI...   NaN    NaN    NaN    NaN   
927 - EXTENSIVE BURNS OR FULL THICKNESS BURNS W...   NaN    NaN    NaN    NaN   
928 - FULL THICKNESS BURN W SKIN GRAFT OR INHAL...   NaN   45.0    NaN   18.0   
929 - FULL THICKNESS BURN W SKIN GRAFT OR INHAL...   NaN    NaN    NaN    NaN   
934 - FULL THICKNESS BURN W/O SKIN GRFT OR INHA...   NaN    NaN    NaN    NaN   
935 - NON-EXTENSIVE BURNS                            NaN   32.0    NaN   23.0   
940 - O.R. PROC W DIAGNOSES OF OTHER CONTACT W ...   NaN    NaN    NaN    NaN   
945 - REHABILITATION W CC/MCC                        NaN    NaN    NaN    NaN   
946 - REHABILITATION W/O CC/MCC                      NaN    NaN    NaN    NaN   
947 - SIGNS & SYMPTOMS W MCC                         NaN   53.0   11.0   16.0   
948 - SIGNS & SYMPTOMS W/O MCC                      43.0  679.0  404.0  353.0   
949 - AFTERCARE W CC/MCC                             NaN    NaN    NaN    NaN   
951 - OTHER FACTORS INFLUENCING HEALTH STATUS        NaN    NaN    NaN    NaN   
956 - LIMB REATTACHMENT, HIP & FEMUR PROC FOR M...   NaN   36.0   12.0   14.0   
957 - OTHER O.R. PROCEDURES FOR MULTIPLE SIGNIF...   NaN   36.0    NaN    NaN   
958 - OTHER O.R. PROCEDURES FOR

In [28]:
total_discharges["Total"] = total_discharges.sum(axis=1)
total_discharges.head()

Provider State                                        AK     AL     AR     AZ  \
DRG Definition                                                                  
001 - HEART TRANSPLANT OR IMPLANT OF HEART ASSI...   NaN   13.0    NaN   20.0   
002 - HEART TRANSPLANT OR IMPLANT OF HEART ASSI...   NaN    NaN    NaN    NaN   
003 - ECMO OR TRACH W MV 96+ HRS OR PDX EXC FAC...  12.0  237.0  128.0  200.0   
004 - TRACH W MV 96+ HRS OR PDX EXC FACE, MOUTH...  11.0  257.0  129.0  127.0   
005 - LIVER TRANSPLANT W MCC OR INTESTINAL TRAN...   NaN   16.0    NaN   17.0   

Provider State                                         CA     CO     CT  \
DRG Definition                                                            
001 - HEART TRANSPLANT OR IMPLANT OF HEART ASSI...  125.0    NaN   29.0   
002 - HEART TRANSPLANT OR IMPLANT OF HEART ASSI...    NaN    NaN    NaN   
003 - ECMO OR TRACH W MV 96+ HRS OR PDX EXC FAC...  710.0  117.0  125.0   
004 - TRACH W MV 96+ HRS OR PDX EXC FACE, MOUTH...  894.0   59.0   59.0   
005 - LIVER TRANSPLANT W MCC OR INTESTINAL TRAN...  106.0   12.0    NaN   

Provider State                                         DC    DE     FL  ...  \
DRG Definition                                                          ...   
001 - HEART TRANSPLANT OR IMPLANT OF HEART ASSI...   31.0   NaN   83.0  ...   
002 - HEART TRANSPLANT OR IMPLANT OF HEART ASSI...    NaN   NaN    NaN  ...   
003 - ECMO OR TRACH W MV 96+ HRS OR PDX EXC FAC...  128.0  79.0  934.0  ...   
004 - TRACH W MV 96+ HRS OR PDX EXC FACE, MOUTH...   81.0  55.0  943.0  ...   
005 - LIVER TRANSPLANT W MCC OR INTESTINAL TRAN...    NaN   NaN   69.0  ...   

Provider State                                         TN      TX    UT  \
DRG Definition                                                            
001 - HEART TRANSPLANT OR IMPLANT OF HEART ASSI...   34.0   206.0   NaN   
002 - HEART TRANSPLANT OR IMPLANT OF HEART ASSI...    NaN     NaN   NaN   
003 - ECMO OR TRACH W MV 96+ HRS OR PDX EXC FAC...  381.0   906.0  54.0   
004 - TRACH W MV 96+ HRS OR PDX EXC FACE, MOUTH...  438.0  1009.0  12.0   
005 - LIVER TRANSPLANT W MCC OR INTESTINAL TRAN...   36.0    46.0   NaN   

Provider State                                         VA    VT    WA     WI  \
DRG Definition                                                                 
001 - HEART TRANSPLANT OR IMPLANT OF HEART ASSI...   61.0   NaN  36.0   21.0   
002 - HEART TRANSPLANT OR IMPLANT OF HEART ASSI...    NaN   NaN   NaN    NaN   
003 - ECMO OR TRACH W MV 96+ HRS OR PDX EXC FAC...  356.0  13.0  74.0  114.0   
004 - TRACH W MV 96+ HRS OR PDX EXC FACE, MOUTH...  247.0   NaN  42.0   84.0   
005 - LIVER TRANSPLANT W MCC OR INTESTINAL TRAN...   13.0   NaN  13.0   16.0   

Provider State                                        WV  WY    Total  
DRG Definition                                                         
001 - HEART TRANSPLANT OR IMPLANT OF HEART ASSI...   NaN NaN   2990.0  
002 - HEART TRANSPLANT OR IMPLANT OF HEART ASSI...   NaN NaN     46.0  
003 - ECMO OR TRACH W MV 96+ HRS OR PDX EXC FAC...  84.0 NaN  23974.0  
004 - TRACH W MV 96+ HRS OR PDX EXC FACE, MOUTH...  50.0 NaN  23548.0  
005 - LIVER TRANSPLANT W MCC OR INTESTINAL TRAN...   NaN NaN   1482.0  

[5 rows x 52 columns]

In [32]:
total_discharges.sort_values(by='Total', ascending=False, inplace=True)
total_discharges.head()

Provider State                                         AK      AL      AR  \
DRG Definition                                                              
470 - MAJOR JOINT REPLACEMENT OR REATTACHMENT O...  855.0  9146.0  5692.0   
871 - SEPTICEMIA OR SEVERE SEPSIS W/O MV 96+ HO...  452.0  6066.0  5187.0   
291 - HEART FAILURE & SHOCK W MCC                   110.0  3894.0  2143.0   
292 - HEART FAILURE & SHOCK W CC                    166.0  4131.0  2382.0   
392 - ESOPHAGITIS, GASTROENT & MISC DIGEST DISO...  182.0  4920.0  2462.0   

Provider State                                           AZ       CA      CO  \
DRG Definition                                                                 
470 - MAJOR JOINT REPLACEMENT OR REATTACHMENT O...  10472.0  32930.0  7793.0   
871 - SEPTICEMIA OR SEVERE SEPSIS W/O MV 96+ HO...   6914.0  45434.0  4400.0   
291 - HEART FAILURE & SHOCK W MCC                    2252.0  14894.0  1273.0   
292 - HEART FAILURE & SHOCK W CC                     2092.0  11654.0  1341.0   
392 - ESOPHAGITIS, GASTROENT & MISC DIGEST DISO...   3050.0  12358.0  1728.0   

Provider State                                          CT      DC      DE  \
DRG Definition                                                               
470 - MAJOR JOINT REPLACEMENT OR REATTACHMENT O...  5689.0  1247.0  2119.0   
871 - SEPTICEMIA OR SEVERE SEPSIS W/O MV 96+ HO...  6390.0   643.0  1556.0   
291 - HEART FAILURE & SHOCK W MCC                   2806.0   529.0  1019.0   
292 - HEART FAILURE & SHOCK W CC                    2714.0   902.0   936.0   
392 - ESOPHAGITIS, GASTROENT & MISC DIGEST DISO...  2723.0   556.0   782.0   

Provider State                                           FL  ...       TN  \
DRG Definition                                               ...            
470 - MAJOR JOINT REPLACEMENT OR REATTACHMENT O...  31086.0  ...  11133.0   
871 - SEPTICEMIA OR SEVERE SEPSIS W/O MV 96+ HO...  25209.0  ...  11295.0   
291 - HEART FAILURE & SHOCK W MCC                   14923.0  ...   5285.0   
292 - HEART FAILURE & SHOCK W CC                    14274.0  ...   4899.0   
392 - ESOPHAGITIS, GASTROENT & MISC DIGEST DISO...  20322.0  ...   4681.0   

Provider State                                           TX      UT       VA  \
DRG Definition                                                                 
470 - MAJOR JOINT REPLACEMENT OR REATTACHMENT O...  29410.0  4455.0  13923.0   
871 - SEPTICEMIA OR SEVERE SEPSIS W/O MV 96+ HO...  30595.0  2780.0  15119.0   
291 - HEART FAILURE & SHOCK W MCC                   13718.0   500.0   6815.0   
292 - HEART FAILURE & SHOCK W CC                    13047.0   548.0   5863.0   
392 - ESOPHAGITIS, GASTROENT & MISC DIGEST DISO...  12692.0   492.0   4884.0   

Provider State                                         VT       WA      WI  \
DRG Definition                                                               
470 - MAJOR JOINT REPLACEMENT OR REATTACHMENT O...  766.0  10027.0  9482.0   
871 - SEPTICEMIA OR SEVERE SEPSIS W/O MV 96+ HO...  739.0  10146.0  6712.0   
291 - HEART FAILURE & SHOCK W MCC                   303.0   3557.0  3028.0   
292 - HEART FAILURE & SHOCK W CC                    318.0   2900.0  3175.0   
392 - ESOPHAGITIS, GASTROENT & MISC DIGEST DISO...  249.0   2435.0  2582.0   

Provider State                                          WV     WY     Total  
DRG Definition                                                               
470 - MAJOR JOINT REPLACEMENT OR REATTACHMENT O...  2925.0  651.0  916518.0  
871 - SEPTICEMIA OR SEVERE SEPSIS W/O MV 96+ HO...  3427.0  474.0  877194.0  
291 - HEART FAILURE & SHOCK W MCC                   1535.0  161.0  397778.0  
292 - HEART FAILURE & SHOCK W CC                    1749.0  212.0  385836.0  
392 - ESOPHAGITIS, GASTROENT & MISC DIGEST DISO...  1632.0  168.0  380750.0  

[5 rows x 52 columns]

In [34]:
del total_discharges['Total']
total_discharges.head()

Provider State                                         AK      AL      AR  \
DRG Definition                                                              
470 - MAJOR JOINT REPLACEMENT OR REATTACHMENT O...  855.0  9146.0  5692.0   
871 - SEPTICEMIA OR SEVERE SEPSIS W/O MV 96+ HO...  452.0  6066.0  5187.0   
291 - HEART FAILURE & SHOCK W MCC                   110.0  3894.0  2143.0   
292 - HEART FAILURE & SHOCK W CC                    166.0  4131.0  2382.0   
392 - ESOPHAGITIS, GASTROENT & MISC DIGEST DISO...  182.0  4920.0  2462.0   

Provider State                                           AZ       CA      CO  \
DRG Definition                                                                 
470 - MAJOR JOINT REPLACEMENT OR REATTACHMENT O...  10472.0  32930.0  7793.0   
871 - SEPTICEMIA OR SEVERE SEPSIS W/O MV 96+ HO...   6914.0  45434.0  4400.0   
291 - HEART FAILURE & SHOCK W MCC                    2252.0  14894.0  1273.0   
292 - HEART FAILURE & SHOCK W CC                     2092.0  11654.0  1341.0   
392 - ESOPHAGITIS, GASTROENT & MISC DIGEST DISO...   3050.0  12358.0  1728.0   

Provider State                                          CT      DC      DE  \
DRG Definition                                                               
470 - MAJOR JOINT REPLACEMENT OR REATTACHMENT O...  5689.0  1247.0  2119.0   
871 - SEPTICEMIA OR SEVERE SEPSIS W/O MV 96+ HO...  6390.0   643.0  1556.0   
291 - HEART FAILURE & SHOCK W MCC                   2806.0   529.0  1019.0   
292 - HEART FAILURE & SHOCK W CC                    2714.0   902.0   936.0   
392 - ESOPHAGITIS, GASTROENT & MISC DIGEST DISO...  2723.0   556.0   782.0   

Provider State                                           FL  ...      SD  \
DRG Definition                                               ...           
470 - MAJOR JOINT REPLACEMENT OR REATTACHMENT O...  31086.0  ...  3200.0   
871 - SEPTICEMIA OR SEVERE SEPSIS W/O MV 96+ HO...  25209.0  ...  1574.0   
291 - HEART FAILURE & SHOCK W MCC                   14923.0  ...   540.0   
292 - HEART FAILURE & SHOCK W CC                    14274.0  ...   511.0   
392 - ESOPHAGITIS, GASTROENT & MISC DIGEST DISO...  20322.0  ...   436.0   

Provider State                                           TN       TX      UT  \
DRG Definition                                                                 
470 - MAJOR JOINT REPLACEMENT OR REATTACHMENT O...  11133.0  29410.0  4455.0   
871 - SEPTICEMIA OR SEVERE SEPSIS W/O MV 96+ HO...  11295.0  30595.0  2780.0   
291 - HEART FAILURE & SHOCK W MCC                    5285.0  13718.0   500.0   
292 - HEART FAILURE & SHOCK W CC                     4899.0  13047.0   548.0   
392 - ESOPHAGITIS, GASTROENT & MISC DIGEST DISO...   4681.0  12692.0   492.0   

Provider State                                           VA     VT       WA  \
DRG Definition                                                                
470 - MAJOR JOINT REPLACEMENT OR REATTACHMENT O...  13923.0  766.0  10027.0   
871 - SEPTICEMIA OR SEVERE SEPSIS W/O MV 96+ HO...  15119.0  739.0  10146.0   
291 - HEART FAILURE & SHOCK W MCC                    6815.0  303.0   3557.0   
292 - HEART FAILURE & SHOCK W CC                     5863.0  318.0   2900.0   
392 - ESOPHAGITIS, GASTROENT & MISC DIGEST DISO...   4884.0  249.0   2435.0   

Provider State                                          WI      WV     WY  
DRG Definition                                                             
470 - MAJOR JOINT REPLACEMENT OR REATTACHMENT O...  9482.0  2925.0  651.0  
871 - SEPTICEMIA OR SEVERE SEPSIS W/O MV 96+ HO...  6712.0  3427.0  474.0  
291 - HEART FAILURE & SHOCK W MCC                   3028.0  1535.0  161.0  
292 - HEART FAILURE & SHOCK W CC                    3175.0  1749.0  212.0  
392 - ESOPHAGITIS, GASTROENT & MISC DIGEST DISO...  2582.0  1632.0  168.0  

[5 rows x 51 columns]

# plot with bqplot

In [35]:
import bqplot
import bqplot.market_map

In [41]:
# scales
x_sc, y_sc = bqplot.OrdinalScale(), bqplot.OrdinalScale()
c_sc = bqplot.ColorScale(scheme='Blues')

# just a color axes for now
c_ax = bqplot.ColorAxis(scale=c_sc, orientation='vertical')

# lets make the map
total_discharges.iloc[0].values, total_discharges.columns.values

# a map of the discharges for the most popular (0th on our list)
# surgery
mmap = bqplot.market_map.MarketMap(color=total_discharges.iloc[0].values, 
                                  names = total_discharges.columns.values,
                                  scales={'color':c_sc}, axes=[c_ax])

import ipywidgets
label = ipywidgets.Label()
def get_data(change):
    #print(change['owner'].selected)
    v = 0.0
    for s in change['owner'].selected:
        v += total_discharges.iloc[0][total_discharges.iloc[0].index == s].values
    if v > 0: # just in case we have not selected anything
        lb = 'Total discharges of ' + total_discharges.iloc[0].name + ' = ' + str(v[0])
        label.value = lb
    
mmap.observe(get_data,'selected')

ipywidgets.VBox([label,mmap])
#mmap

VkJveChjaGlsZHJlbj0oTGFiZWwodmFsdWU9dScnKSwgTWFya2V0TWFwKGF4ZXM9W0NvbG9yQXhpcyhvcmllbnRhdGlvbj0ndmVydGljYWwnLCBzY2FsZT1Db2xvclNjYWxlKHNjaGVtZT11J0LigKY=


# ipyleaflets

In [43]:
#!pip install ipyleaflet
from ipyleaflet import *

m = Map(center=(52, 10), zoom=8, basemap=basemaps.Hydda.Full)

# plot street maps
streets = basemap_to_tiles(basemaps.Strava.All)
m.add_layer(streets)

m

TWFwKGJhc2VtYXA9eyd1cmwnOiAnaHR0cDovL3tzfS50aWxlLm9wZW5zdHJlZXRtYXAuc2UvaHlkZGEvZnVsbC97en0ve3h9L3t5fS5wbmcnLCAnYXR0cmlidXRpb24nOiAnVGlsZXMgY291cnTigKY=


# Onto network data!

In [59]:
node_data = [
    {"label": "Luke Skywalker", "media": "Star Wars", "shape": "rect"},
    {"label": "Jean-Luc Picard", "media": "Star Trek", "shape": "rect"},
    {"label": "Doctor Who", "media": "Doctor Who", "shape": "rect"},
    {"label": "Pikachu", "media": "Detective Pikachu", "shape": "circle"},
]

# lets put in some edges or links
link_data = [{'source':0, 'target': 1}, {'source':0, 'target':3}]

tooltip = bqplot.Tooltip(fields=['media'])
graph = bqplot.Graph(node_data = node_data, colors=["red", "red", "red","red"], 
                    link_data=link_data, tooltip=tooltip)

# link type
graph.link_type='line'
# take off directionally of links
graph.directed = False
# change the repulsive charge
graph.charge = -300

# we can use widgets to label
label = ipywidgets.Label()

def printstuff(obj, element):
    #print(element)
    label.value = 'Media = ' + element['data']['media']
    
graph.on_element_click(printstuff)
    
fig = bqplot.Figure(marks=[graph])
#fig
ipywidgets.VBox([label,fig])

VkJveChjaGlsZHJlbj0oTGFiZWwodmFsdWU9dScnKSwgRmlndXJlKGZpZ19tYXJnaW49eyd0b3AnOiA2MCwgJ3JpZ2h0JzogNjAsICdib3R0b20nOiA2MCwgJ2xlZnQnOiA2MH0sIGxheW91dD3igKY=


# Actual network data

In [75]:
#filename = 'facebook_combined_sm000090_000010.txt'
filename = 'facebook_combined_sm000030_000000.txt'

network = pd.read_csv('/Users/jillnaiman1/Downloads/' + filename, 
                     sep=' ', names=['ind1','ind2'])
network

ind1  ind2
0      0     1
1      0     1
2      0     2
3      0     3
4      0     4
5      0     5
6      0     6
7      0     7
8      0     8
9      0     9
10     0    10
11     0    11
12     0    12
13     0    13
14     0    14
15     0    15
16     0    16
17     0    17
18     0    18
19     0    19
20     0    20
21     0    21
22     0    22
23     0    23
24     0    24
25     0    25
26     0    26
27     0    27
28     0    28
29     0    29
30     0    30
31     2    20
32     3     9
33     3    25
34     3    26
35     7    22
36     9    21
37     9    25
38     9    26
39     9    30
40    13    21
41    13    26
42    14    20
43    14    28
44    16    29
45    17    19
46    21    25
47    21    26
48    25    26

In [76]:
node_data = []
link_data = []
color_data = []

# fill nodes
maxNet = max([network['ind1'].max(),network['ind2'].max()])
for i in range(maxNet+1):
    #node_data.append({'label':str(i), "shape":"circle"})
    node_data.append({'label':str(i), 'shape_attrs':{'r':8} })
    color_data.append('blue')
    
# fill links 
for i in range(len(network)):
    source_id = network.iloc[i]['ind1']
    target_id = network.iloc[i]['ind2']
    link_data.append({'source':source_id, 'target':target_id})
    
#node_data

In [77]:
graph = bqplot.Graph(node_data=node_data, link_data=link_data, colors=color_data)

fig = bqplot.Figure(marks=[graph])
fig.layout.min_width='1000px'
fig.layout.min_height='900px'

# take out directionality
graph.directed = False
# no arcs => lines
graph.link_type='line'
# shorter links
graph.link_distance=50
# closer together points
graph.charge = -100 # default is -300

fig

RmlndXJlKGZpZ19tYXJnaW49eyd0b3AnOiA2MCwgJ3JpZ2h0JzogNjAsICdib3R0b20nOiA2MCwgJ2xlZnQnOiA2MH0sIGxheW91dD1MYXlvdXQobWluX2hlaWdodD11JzkwMHB4JywgbWluX3figKY=
